Import Module

In [2]:
from tensorflow.keras.layers import Dense, Flatten, Activation, GlobalAveragePooling2D
from tensorflow.keras.datasets.cifar100 import load_data
from tensorflow.keras.applications import MobileNetV2, ResNet50, InceptionV3, VGG16, EfficientNetB0, DenseNet121, Xception, NASNetMobile, InceptionResNetV2, EfficientNetV2B0
from tensorflow.keras.models import Model;
from tensorflow.keras.utils import to_categorical
from tensorflow.keras.optimizers import Adam
import tensorflow as tf
import numpy as np
import random

2025-05-25 07:10:13.865809: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:467] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1748135413.884942   29347 cuda_dnn.cc:8579] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1748135413.891068   29347 cuda_blas.cc:1407] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
W0000 00:00:1748135413.903700   29347 computation_placer.cc:177] computation placer already registered. Please check linkage and avoid linking the same target more than once.
W0000 00:00:1748135413.903716   29347 computation_placer.cc:177] computation placer already registered. Please check linkage and avoid linking the same target more than once.
W0000 00:00:1748135413.903718   29347 computation_placer.cc:177] computation placer alr

In [3]:
SEED =  50
random.seed(SEED)
np.random.seed(SEED)
tf.random.set_seed(SEED)

In [4]:
(x_train, y_train), (x_test, y_test) = load_data(label_mode='fine')

In [5]:
classes = random.sample(range(100), 20)

In [6]:
def filter_classes(x,y,selected):
    x_filtered = []
    y_filtered = []
    class_map = {cls: idx for idx, cls in enumerate(selected)}
    for img, label in zip(x,y):
        if label[0] in selected:
            x_filtered.append(img)
            y_filtered.append(class_map[label[0]])
    return np.array(x_filtered), np.array(y_filtered)

In [7]:
x_train, y_train = filter_classes(x_train, y_train, classes)
x_test, y_test = filter_classes(x_test, y_test, classes)

In [8]:
def preprocess_data(x,y):
    x = tf.image.resize(x,(224,224))/255.0
    y = to_categorical(y, num_classes=20)
    return x,y

In [9]:
x_train, y_train = preprocess_data(x_train, y_train)
x_test, y_test = preprocess_data(x_test, y_test)

W0000 00:00:1748135439.713028   29347 gpu_device.cc:2341] Cannot dlopen some GPU libraries. Please make sure the missing libraries mentioned above are installed properly if you would like to use GPU. Follow the guide at https://www.tensorflow.org/install/gpu for how to download and setup the required libraries for your platform.
Skipping registering GPU devices...
2025-05-25 07:10:39.832631: W external/local_xla/xla/tsl/framework/cpu_allocator_impl.cc:83] Allocation of 6021120000 exceeds 10% of free system memory.
2025-05-25 07:10:52.547169: W external/local_xla/xla/tsl/framework/cpu_allocator_impl.cc:83] Allocation of 6021120000 exceeds 10% of free system memory.
2025-05-25 07:11:06.210960: W external/local_xla/xla/tsl/framework/cpu_allocator_impl.cc:83] Allocation of 1204224000 exceeds 10% of free system memory.
2025-05-25 07:11:07.333603: W external/local_xla/xla/tsl/framework/cpu_allocator_impl.cc:83] Allocation of 1204224000 exceeds 10% of free system memory.


1. MobileNetV2

In [10]:
model_0 = MobileNetV2(weights='imagenet', include_top=False, input_shape=(224,224,3))
model_0.trainable = False # Freeze base layers

In [11]:
inputs = model_0.input
output = model_0.output
x = GlobalAveragePooling2D()(output)
outputs = Dense(20, activation='softmax')(x)
model = Model(inputs, outputs)
model.summary(show_trainable=True)

Model: "functional"

┏━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━┳━━━━━━━━━━━━━━━━┳━━━━━━━┓
┃ Layer (type)      ┃ Output Shape    ┃   Param # ┃ Connected to   ┃ Trai… ┃
┡━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━╇━━━━━━━━━━━━━━━━╇━━━━━━━┩
│ input_layer       │ (None, 224,     │         0 │ -              │   -   │
│ (InputLayer)      │ 224, 3)         │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ Conv1 (Conv2D)    │ (None, 112,     │       864 │ input_layer[0… │   N   │
│                   │ 112, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ bn_Conv1          │ (None, 112,     │       128 │ Conv1[0][0]    │   N   │
│ (BatchNormalizat… │ 112, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ Conv1_relu (ReLU) │ (None, 112,     │         0 │ bn_Conv1[0][0] │   -   │
│                   │ 112, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ expanded_conv_de… │ (None, 112,     │       288 │ Conv1_relu[0]… │   N   │
│ (DepthwiseConv2D) │ 112, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ expanded_conv_de… │ (None, 112,     │       128 │ expanded_conv… │   N   │
│ (BatchNormalizat… │ 112, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ expanded_conv_de… │ (None, 112,     │         0 │ expanded_conv… │   -   │
│ (ReLU)            │ 112, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ expanded_conv_pr… │ (None, 112,     │       512 │ expanded_conv… │   N   │
│ (Conv2D)          │ 112, 16)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ expanded_conv_pr… │ (None, 112,     │        64 │ expanded_conv… │   N   │
│ (BatchNormalizat… │ 112, 16)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block_1_expand    │ (None, 112,     │     1,536 │ expanded_conv… │   N   │
│ (Conv2D)          │ 112, 96)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block_1_expand_BN │ (None, 112,     │       384 │ block_1_expan… │   N   │
│ (BatchNormalizat… │ 112, 96)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block_1_expand_r… │ (None, 112,     │         0 │ block_1_expan… │   -   │
│ (ReLU)            │ 112, 96)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block_1_pad       │ (None, 113,     │         0 │ block_1_expan… │   -   │
│ (ZeroPadding2D)   │ 113, 96)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block_1_depthwise │ (None, 56, 56,  │       864 │ block_1_pad[0… │   N   │
│ (DepthwiseConv2D) │ 96)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block_1_depthwis… │ (None, 56, 56,  │       384 │ block_1_depth… │   N   │
│ (BatchNormalizat… │ 96)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block_1_depthwis… │ (None, 56, 56,  │         0 │ block_1_depth… │   -   │
│ (ReLU)            │ 96)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block_1_project   │ (None, 56, 56,  │     2,304 │ block_1_depth… │   N 

 Total params: 2,283,604 (8.71 MB)

 Trainable params: 25,620 (100.08 KB)

 Non-trainable params: 2,257,984 (8.61 MB)

In [12]:
model.compile(optimizer=Adam(1e-4), loss='categorical_crossentropy', metrics=['accuracy'])
history = model.fit(x_train, y_train, epochs=5, batch_size=32, validation_split=0.2)

Epoch 1/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 141s 554ms/step - accuracy: 0.1589 - loss: 2.7636 - val_accuracy: 0.4815 - val_loss: 1.8746
Epoch 2/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 142s 567ms/step - accuracy: 0.5297 - loss: 1.6899 - val_accuracy: 0.6195 - val_loss: 1.3779
Epoch 3/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 137s 547ms/step - accuracy: 0.6502 - loss: 1.2743 - val_accuracy: 0.6655 - val_loss: 1.1616
Epoch 4/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 135s 541ms/step - accuracy: 0.6860 - loss: 1.0786 - val_accuracy: 0.6910 - val_loss: 1.0443
Epoch 5/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 135s 541ms/step - accuracy: 0.7096 - loss: 0.9651 - val_accuracy: 0.7070 - val_loss: 0.9701


In [13]:
loss, acc = model.evaluate(x_test, y_test)
print(f"Test Accuracy for MobileNetV2: {acc*100:.2f}%")

63/63 ━━━━━━━━━━━━━━━━━━━━ 27s 431ms/step - accuracy: 0.7066 - loss: 0.9543
Test Accuracy for MobileNetV2: 69.80%


ResNet50

2. Pretrained model ResNet50

In [12]:
model_resnet = ResNet50(weights='imagenet', include_top=False, input_shape=(224,224,3))
model_resnet.trainable = False

In [13]:
inputs = model_resnet.input
outputs = model_resnet.output

x = GlobalAveragePooling2D()(outputs)
outputs = Dense(20, activation='softmax')(x)
model = Model(inputs, outputs)
model.summary()

Model: "functional_1"

┏━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)        ┃ Output Shape      ┃    Param # ┃ Connected to      ┃
┡━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━┩
│ input_layer_1       │ (None, 224, 224,  │          0 │ -                 │
│ (InputLayer)        │ 3)                │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv1_pad           │ (None, 230, 230,  │          0 │ input_layer_1[0]… │
│ (ZeroPadding2D)     │ 3)                │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv1_conv (Conv2D) │ (None, 112, 112,  │      9,472 │ conv1_pad[0][0]   │
│                     │ 64)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv1_bn            │ (None, 112, 112,  │        256 │ conv1_conv[0][0]  │
│ (BatchNormalizatio… │ 64)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv1_relu          │ (None, 112, 112,  │          0 │ conv1_bn[0][0]    │
│ (Activation)        │ 64)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ pool1_pad           │ (None, 114, 114,  │          0 │ conv1_relu[0][0]  │
│ (ZeroPadding2D)     │ 64)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ pool1_pool          │ (None, 56, 56,    │          0 │ pool1_pad[0][0]   │
│ (MaxPooling2D)      │ 64)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2_block1_1_conv │ (None, 56, 56,    │      4,160 │ pool1_pool[0][0]  │
│ (Conv2D)            │ 64)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2_block1_1_bn   │ (None, 56, 56,    │        256 │ conv2_block1_1_c… │
│ (BatchNormalizatio… │ 64)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2_block1_1_relu │ (None, 56, 56,    │          0 │ conv2_block1_1_b… │
│ (Activation)        │ 64)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2_block1_2_conv │ (None, 56, 56,    │     36,928 │ conv2_block1_1_r… │
│ (Conv2D)            │ 64)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2_block1_2_bn   │ (None, 56, 56,    │        256 │ conv2_block1_2_c… │
│ (BatchNormalizatio… │ 64)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2_block1_2_relu │ (None, 56, 56,    │          0 │ conv2_block1_2_b… │
│ (Activation)        │ 64)               │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2_block1_0_conv │ (None, 56, 56,    │     16,640 │ pool1_pool[0][0]  │
│ (Conv2D)            │ 256)              │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2_block1_3_conv │ (None, 56, 56,    │     16,640 │ conv2_block1_2_r… │
│ (Conv2D)            │ 256)              │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2_block1_0_bn   │ (None, 56, 56,    │      1,024 │ conv2_block1_0_c… │
│ (BatchNormalizatio… │ 256)              │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ conv2_block1_3_bn   │ (None, 56, 56,    │      1,024 │ conv2_block1_3_c

 Total params: 23,628,692 (90.14 MB)

 Trainable params: 40,980 (160.08 KB)

 Non-trainable params: 23,587,712 (89.98 MB)

In [16]:
model.compile(optimizer=Adam(1e-4), loss='categorical_crossentropy', metrics=['accuracy'])
history = model.fit(x_train, y_train, batch_size=32, epochs=5, validation_split=0.2)

Epoch 1/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 396s 2s/step - accuracy: 0.0494 - loss: 3.0520 - val_accuracy: 0.0525 - val_loss: 2.9954
Epoch 2/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 386s 2s/step - accuracy: 0.0559 - loss: 2.9940 - val_accuracy: 0.0550 - val_loss: 2.9915
Epoch 3/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 385s 2s/step - accuracy: 0.0588 - loss: 2.9897 - val_accuracy: 0.0555 - val_loss: 2.9877
Epoch 4/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 385s 2s/step - accuracy: 0.0630 - loss: 2.9855 - val_accuracy: 0.0565 - val_loss: 2.9840
Epoch 5/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 392s 2s/step - accuracy: 0.0677 - loss: 2.9814 - val_accuracy: 0.0560 - val_loss: 2.9803


In [17]:
loss, acc = model.evaluate(x_test, y_test)
print(f"Test Accuracy for ResNet50: {acc*100:.2f}%")

63/63 ━━━━━━━━━━━━━━━━━━━━ 78s 1s/step - accuracy: 0.0598 - loss: 2.9757
Test Accuracy for ResNet50: 5.65%


3. VGG16 model

In [14]:
model_vgg16 = VGG16(weights='imagenet', include_top=False, input_shape=(224,224,3))
model_vgg16.trainable = False

In [16]:
inputs = model_vgg16.input
outputs = model_vgg16.output
x = GlobalAveragePooling2D()(outputs)
outputs = Dense(20, activation='softmax')(x)
model = Model(inputs, outputs)
model.summary(show_trainable=True)

Model: "functional_3"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━┳━━━━━━━┓
┃ Layer (type)                ┃ Output Shape          ┃    Param # ┃ Trai… ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━╇━━━━━━━┩
│ input_layer_2 (InputLayer)  │ (None, 224, 224, 3)   │          0 │   -   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block1_conv1 (Conv2D)       │ (None, 224, 224, 64)  │      1,792 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block1_conv2 (Conv2D)       │ (None, 224, 224, 64)  │     36,928 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block1_pool (MaxPooling2D)  │ (None, 112, 112, 64)  │          0 │   -   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block2_conv1 (Conv2D)       │ (None, 112, 112, 128) │     73,856 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block2_conv2 (Conv2D)       │ (None, 112, 112, 128) │    147,584 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block2_pool (MaxPooling2D)  │ (None, 56, 56, 128)   │          0 │   -   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block3_conv1 (Conv2D)       │ (None, 56, 56, 256)   │    295,168 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block3_conv2 (Conv2D)       │ (None, 56, 56, 256)   │    590,080 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block3_conv3 (Conv2D)       │ (None, 56, 56, 256)   │    590,080 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block3_pool (MaxPooling2D)  │ (None, 28, 28, 256)   │          0 │   -   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block4_conv1 (Conv2D)       │ (None, 28, 28, 512)   │  1,180,160 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block4_conv2 (Conv2D)       │ (None, 28, 28, 512)   │  2,359,808 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block4_conv3 (Conv2D)       │ (None, 28, 28, 512)   │  2,359,808 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block4_pool (MaxPooling2D)  │ (None, 14, 14, 512)   │          0 │   -   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block5_conv1 (Conv2D)       │ (None, 14, 14, 512)   │  2,359,808 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block5_conv2 (Conv2D)       │ (None, 14, 14, 512)   │  2,359,808 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block5_conv3 (Conv2D)       │ (None, 14, 14, 512)   │  2,359,808 │   N   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ block5_pool (MaxPooling2D)  │ (None, 7, 7, 512)     │          0 │   -   │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ global_average_pooling2d_3  │ (None, 512)           │          0 │   -   │
│ (GlobalAveragePooling2D)    │                       │            │       │
├─────────────────────────────┼───────────────────────┼────────────┼───────┤
│ dense_3 (Dense)             │ (None, 20)            │     10,260 │   Y   │
└─────────────────────────────┴───────────────────────┴────────────┴───────┘

 Total params: 14,724,948 (56.17 MB)

 Trainable params: 10,260 (40.08 KB)

 Non-trainable params: 14,714,688 (56.13 MB)

In [20]:
model.compile(optimizer=Adam(1e-4), loss='categorical_crossentropy', metrics=['accuracy'])
history = model.fit(x_train, y_train, batch_size=32, epochs=5, validation_split = 0.2)

Epoch 1/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 972s 4s/step - accuracy: 0.0509 - loss: 3.1013 - val_accuracy: 0.0470 - val_loss: 2.9597
Epoch 2/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 960s 4s/step - accuracy: 0.0882 - loss: 2.9465 - val_accuracy: 0.1675 - val_loss: 2.9100
Epoch 3/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 962s 4s/step - accuracy: 0.1821 - loss: 2.8975 - val_accuracy: 0.2035 - val_loss: 2.8709
Epoch 4/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 951s 4s/step - accuracy: 0.2223 - loss: 2.8573 - val_accuracy: 0.2290 - val_loss: 2.8337
Epoch 5/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 919s 4s/step - accuracy: 0.2398 - loss: 2.8196 - val_accuracy: 0.2480 - val_loss: 2.7986


In [21]:
loss, acc = model.evaluate(x_test, y_test)
print(f"Test Accuracy for VGG16: {acc*100:.2f}%")

63/63 ━━━━━━━━━━━━━━━━━━━━ 183s 3s/step - accuracy: 0.2476 - loss: 2.7937
Test Accuracy for VGG16: 25.80%


4. EfficientNetB0 Model

In [17]:
model_efficientnet = EfficientNetB0(weights='imagenet', include_top=False, input_shape=(224,224,3))
model_efficientnet.trainable = False

In [18]:
inputs = model_efficientnet.input
outputs = model_efficientnet.output
x = GlobalAveragePooling2D()(outputs)
outputs = Dense(20, activation='softmax')(x)
model = Model(inputs, outputs)
model.summary(show_trainable=True)

Model: "functional_4"

┏━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━┳━━━━━━━━━━━━━━━━┳━━━━━━━┓
┃ Layer (type)      ┃ Output Shape    ┃   Param # ┃ Connected to   ┃ Trai… ┃
┡━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━╇━━━━━━━━━━━━━━━━╇━━━━━━━┩
│ input_layer_3     │ (None, 224,     │         0 │ -              │   -   │
│ (InputLayer)      │ 224, 3)         │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ rescaling         │ (None, 224,     │         0 │ input_layer_3… │   -   │
│ (Rescaling)       │ 224, 3)         │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ normalization     │ (None, 224,     │         7 │ rescaling[0][… │   N   │
│ (Normalization)   │ 224, 3)         │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ rescaling_1       │ (None, 224,     │         0 │ normalization… │   -   │
│ (Rescaling)       │ 224, 3)         │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ stem_conv_pad     │ (None, 225,     │         0 │ rescaling_1[0… │   -   │
│ (ZeroPadding2D)   │ 225, 3)         │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ stem_conv         │ (None, 112,     │       864 │ stem_conv_pad… │   N   │
│ (Conv2D)          │ 112, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ stem_bn           │ (None, 112,     │       128 │ stem_conv[0][… │   N   │
│ (BatchNormalizat… │ 112, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ stem_activation   │ (None, 112,     │         0 │ stem_bn[0][0]  │   -   │
│ (Activation)      │ 112, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block1a_dwconv    │ (None, 112,     │       288 │ stem_activati… │   N   │
│ (DepthwiseConv2D) │ 112, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block1a_bn        │ (None, 112,     │       128 │ block1a_dwcon… │   N   │
│ (BatchNormalizat… │ 112, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block1a_activati… │ (None, 112,     │         0 │ block1a_bn[0]… │   -   │
│ (Activation)      │ 112, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block1a_se_squee… │ (None, 32)      │         0 │ block1a_activ… │   -   │
│ (GlobalAveragePo… │                 │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block1a_se_resha… │ (None, 1, 1,    │         0 │ block1a_se_sq… │   -   │
│ (Reshape)         │ 32)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block1a_se_reduce │ (None, 1, 1, 8) │       264 │ block1a_se_re… │   N   │
│ (Conv2D)          │                 │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block1a_se_expand │ (None, 1, 1,    │       288 │ block1a_se_re… │   N   │
│ (Conv2D)          │ 32)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block1a_se_excite │ (None, 112,     │         0 │ block1a_activ… │   -   │
│ (Multiply)        │ 112, 32)        │           │ block1a_se_ex… │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block1a_project_… │ (None, 112,     │       512 │ block1a_se_ex… │   N 

 Total params: 4,075,191 (15.55 MB)

 Trainable params: 25,620 (100.08 KB)

 Non-trainable params: 4,049,571 (15.45 MB)

In [24]:
model.compile(optimizer=Adam(1e-4), loss='categorical_crossentropy', metrics=['accuracy'])
history = model.fit(x_train, y_train, batch_size=32, epochs=5, validation_split = 0.2)

Epoch 1/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 211s 825ms/step - accuracy: 0.0489 - loss: 3.0101 - val_accuracy: 0.0525 - val_loss: 3.0005
Epoch 2/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 205s 822ms/step - accuracy: 0.0521 - loss: 3.0002 - val_accuracy: 0.0525 - val_loss: 3.0001
Epoch 3/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 205s 821ms/step - accuracy: 0.0548 - loss: 2.9999 - val_accuracy: 0.0525 - val_loss: 3.0005
Epoch 4/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 218s 872ms/step - accuracy: 0.0503 - loss: 2.9995 - val_accuracy: 0.0525 - val_loss: 3.0004
Epoch 5/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 208s 830ms/step - accuracy: 0.0491 - loss: 3.0002 - val_accuracy: 0.0525 - val_loss: 3.0001


In [25]:
loss, acc = model.evaluate(x_test, y_test)
print(f"Test Accuracy for EfficientNetB0: {acc*100:.2f}%")

63/63 ━━━━━━━━━━━━━━━━━━━━ 41s 643ms/step - accuracy: 0.0528 - loss: 2.9970
Test Accuracy for EfficientNetB0: 5.00%


5. DenseNet121 Model

In [19]:
model_densenet = DenseNet121(weights='imagenet', include_top=False, input_shape=(224,224,3))
model_densenet.trainable = False

In [20]:
inputs = model_densenet.input
outputs = model_densenet.output
x = GlobalAveragePooling2D()(outputs)
outputs = Dense(20, activation='softmax')(x)
model = Model(inputs, outputs)
model.summary(show_trainable=True)

Model: "functional_5"

┏━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━┳━━━━━━━━━━━━━━━━┳━━━━━━━┓
┃ Layer (type)      ┃ Output Shape    ┃   Param # ┃ Connected to   ┃ Trai… ┃
┡━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━╇━━━━━━━━━━━━━━━━╇━━━━━━━┩
│ input_layer_4     │ (None, 224,     │         0 │ -              │   -   │
│ (InputLayer)      │ 224, 3)         │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ zero_padding2d    │ (None, 230,     │         0 │ input_layer_4… │   -   │
│ (ZeroPadding2D)   │ 230, 3)         │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ conv1_conv        │ (None, 112,     │     9,408 │ zero_padding2… │   N   │
│ (Conv2D)          │ 112, 64)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ conv1_bn          │ (None, 112,     │       256 │ conv1_conv[0]… │   N   │
│ (BatchNormalizat… │ 112, 64)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ conv1_relu        │ (None, 112,     │         0 │ conv1_bn[0][0] │   -   │
│ (Activation)      │ 112, 64)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ zero_padding2d_1  │ (None, 114,     │         0 │ conv1_relu[0]… │   -   │
│ (ZeroPadding2D)   │ 114, 64)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ pool1             │ (None, 56, 56,  │         0 │ zero_padding2… │   -   │
│ (MaxPooling2D)    │ 64)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ conv2_block1_0_bn │ (None, 56, 56,  │       256 │ pool1[0][0]    │   N   │
│ (BatchNormalizat… │ 64)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ conv2_block1_0_r… │ (None, 56, 56,  │         0 │ conv2_block1_… │   -   │
│ (Activation)      │ 64)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ conv2_block1_1_c… │ (None, 56, 56,  │     8,192 │ conv2_block1_… │   N   │
│ (Conv2D)          │ 128)            │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ conv2_block1_1_bn │ (None, 56, 56,  │       512 │ conv2_block1_… │   N   │
│ (BatchNormalizat… │ 128)            │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ conv2_block1_1_r… │ (None, 56, 56,  │         0 │ conv2_block1_… │   -   │
│ (Activation)      │ 128)            │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ conv2_block1_2_c… │ (None, 56, 56,  │    36,864 │ conv2_block1_… │   N   │
│ (Conv2D)          │ 32)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ conv2_block1_con… │ (None, 56, 56,  │         0 │ pool1[0][0],   │   -   │
│ (Concatenate)     │ 96)             │           │ conv2_block1_… │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ conv2_block2_0_bn │ (None, 56, 56,  │       384 │ conv2_block1_… │   N   │
│ (BatchNormalizat… │ 96)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ conv2_block2_0_r… │ (None, 56, 56,  │         0 │ conv2_block2_… │   -   │
│ (Activation)      │ 96)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ conv2_block2_1_c… │ (None, 56, 56,  │    12,288 │ conv2_block2_… │   N 

 Total params: 7,058,004 (26.92 MB)

 Trainable params: 20,500 (80.08 KB)

 Non-trainable params: 7,037,504 (26.85 MB)

In [28]:
model.compile(optimizer=Adam(1e-4), loss='categorical_crossentropy', metrics=['accuracy'])
history = model.fit(x_train, y_train, batch_size=32, epochs=5, validation_split = 0.2)

Epoch 1/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 433s 2s/step - accuracy: 0.0696 - loss: 3.2561 - val_accuracy: 0.2720 - val_loss: 2.4387
Epoch 2/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 425s 2s/step - accuracy: 0.3429 - loss: 2.3053 - val_accuracy: 0.4885 - val_loss: 1.8874
Epoch 3/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 425s 2s/step - accuracy: 0.5201 - loss: 1.8106 - val_accuracy: 0.5770 - val_loss: 1.5658
Epoch 4/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 402s 2s/step - accuracy: 0.6045 - loss: 1.5159 - val_accuracy: 0.6320 - val_loss: 1.3678
Epoch 5/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 401s 2s/step - accuracy: 0.6504 - loss: 1.3294 - val_accuracy: 0.6595 - val_loss: 1.2363


In [29]:
loss, acc = model.evaluate(x_test, y_test)
print(f"Test Accuracy for DenseNet121: {acc*100:.2f}%")

63/63 ━━━━━━━━━━━━━━━━━━━━ 81s 1s/step - accuracy: 0.6493 - loss: 1.2759
Test Accuracy for DenseNet121: 66.05%


6. NASNetMobile Model

In [21]:
model_nasnet = NASNetMobile(weights='imagenet', include_top=False, input_shape=(224,224,3))
model_nasnet.trainable = False

In [22]:
inputs = model_nasnet.input
outputs = model_nasnet.output
x = GlobalAveragePooling2D()(outputs)
outputs = Dense(20, activation='softmax')(x)
model = Model(inputs, outputs)
model.summary(show_trainable=True)

Model: "functional_6"

┏━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━┳━━━━━━━━━━━━━━━━┳━━━━━━━┓
┃ Layer (type)      ┃ Output Shape    ┃   Param # ┃ Connected to   ┃ Trai… ┃
┡━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━╇━━━━━━━━━━━━━━━━╇━━━━━━━┩
│ input_layer_5     │ (None, 224,     │         0 │ -              │   -   │
│ (InputLayer)      │ 224, 3)         │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ stem_conv1        │ (None, 111,     │       864 │ input_layer_5… │   N   │
│ (Conv2D)          │ 111, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ stem_bn1          │ (None, 111,     │       128 │ stem_conv1[0]… │   N   │
│ (BatchNormalizat… │ 111, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ activation        │ (None, 111,     │         0 │ stem_bn1[0][0] │   -   │
│ (Activation)      │ 111, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ reduction_conv_1… │ (None, 111,     │       352 │ activation[0]… │   N   │
│ (Conv2D)          │ 111, 11)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ reduction_bn_1_s… │ (None, 111,     │        44 │ reduction_con… │   N   │
│ (BatchNormalizat… │ 111, 11)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ activation_1      │ (None, 111,     │         0 │ reduction_bn_… │   -   │
│ (Activation)      │ 111, 11)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ activation_3      │ (None, 111,     │         0 │ stem_bn1[0][0] │   -   │
│ (Activation)      │ 111, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ separable_conv_1… │ (None, 115,     │         0 │ activation_1[… │   -   │
│ (ZeroPadding2D)   │ 115, 11)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ separable_conv_1… │ (None, 117,     │         0 │ activation_3[… │   -   │
│ (ZeroPadding2D)   │ 117, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ separable_conv_1… │ (None, 56, 56,  │       396 │ separable_con… │   N   │
│ (SeparableConv2D) │ 11)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ separable_conv_1… │ (None, 56, 56,  │     1,920 │ separable_con… │   N   │
│ (SeparableConv2D) │ 11)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ separable_conv_1… │ (None, 56, 56,  │        44 │ separable_con… │   N   │
│ (BatchNormalizat… │ 11)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ separable_conv_1… │ (None, 56, 56,  │        44 │ separable_con… │   N   │
│ (BatchNormalizat… │ 11)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ activation_2      │ (None, 56, 56,  │         0 │ separable_con… │   -   │
│ (Activation)      │ 11)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ activation_4      │ (None, 56, 56,  │         0 │ separable_con… │   -   │
│ (Activation)      │ 11)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ separable_conv_2… │ (None, 56, 56,  │       396 │ activation_2[… │   N 

 Total params: 4,290,856 (16.37 MB)

 Trainable params: 21,140 (82.58 KB)

 Non-trainable params: 4,269,716 (16.29 MB)

In [32]:
model.compile(optimizer=Adam(1e-4), loss='categorical_crossentropy', metrics=['accuracy'])
history = model.fit(x_train, y_train, batch_size=32, epochs=5, validation_split = 0.2)

Epoch 1/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 174s 651ms/step - accuracy: 0.1883 - loss: 2.7652 - val_accuracy: 0.5370 - val_loss: 1.9510
Epoch 2/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 149s 595ms/step - accuracy: 0.5900 - loss: 1.7513 - val_accuracy: 0.6660 - val_loss: 1.3989
Epoch 3/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 148s 594ms/step - accuracy: 0.6887 - loss: 1.2889 - val_accuracy: 0.7110 - val_loss: 1.1453
Epoch 4/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 149s 596ms/step - accuracy: 0.7213 - loss: 1.0684 - val_accuracy: 0.7270 - val_loss: 1.0111
Epoch 5/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 149s 597ms/step - accuracy: 0.7413 - loss: 0.9451 - val_accuracy: 0.7365 - val_loss: 0.9291


In [33]:
loss, acc = model.evaluate(x_test, y_test)
print(f"Test Accuracy for NASNetMobile: {acc*100:.2f}%")

63/63 ━━━━━━━━━━━━━━━━━━━━ 30s 477ms/step - accuracy: 0.7293 - loss: 0.9526
Test Accuracy for NASNetMobile: 72.85%


7. EfficientNetV2B0

In [23]:
model_efficientv2 = EfficientNetV2B0(weights='imagenet', include_top=False, input_shape=(224,224,3))
model_efficientv2.trainable = False

In [24]:
inputs = model_efficientv2.input
outputs = model_efficientv2.output
x = GlobalAveragePooling2D()(outputs)
outputs = Dense(20, activation='softmax')(x)
model = Model(inputs, outputs)
model.summary(show_trainable=True)

Model: "functional_7"

┏━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━┳━━━━━━━━━━━━━━━━┳━━━━━━━┓
┃ Layer (type)      ┃ Output Shape    ┃   Param # ┃ Connected to   ┃ Trai… ┃
┡━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━╇━━━━━━━━━━━━━━━━╇━━━━━━━┩
│ input_layer_6     │ (None, 224,     │         0 │ -              │   -   │
│ (InputLayer)      │ 224, 3)         │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ rescaling_2       │ (None, 224,     │         0 │ input_layer_6… │   -   │
│ (Rescaling)       │ 224, 3)         │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ normalization_1   │ (None, 224,     │         0 │ rescaling_2[0… │   -   │
│ (Normalization)   │ 224, 3)         │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ stem_conv         │ (None, 112,     │       864 │ normalization… │   N   │
│ (Conv2D)          │ 112, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ stem_bn           │ (None, 112,     │       128 │ stem_conv[0][… │   N   │
│ (BatchNormalizat… │ 112, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ stem_activation   │ (None, 112,     │         0 │ stem_bn[0][0]  │   -   │
│ (Activation)      │ 112, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block1a_project_… │ (None, 112,     │     4,608 │ stem_activati… │   N   │
│ (Conv2D)          │ 112, 16)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block1a_project_… │ (None, 112,     │        64 │ block1a_proje… │   N   │
│ (BatchNormalizat… │ 112, 16)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block1a_project_… │ (None, 112,     │         0 │ block1a_proje… │   -   │
│ (Activation)      │ 112, 16)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block2a_expand_c… │ (None, 56, 56,  │     9,216 │ block1a_proje… │   N   │
│ (Conv2D)          │ 64)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block2a_expand_bn │ (None, 56, 56,  │       256 │ block2a_expan… │   N   │
│ (BatchNormalizat… │ 64)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block2a_expand_a… │ (None, 56, 56,  │         0 │ block2a_expan… │   -   │
│ (Activation)      │ 64)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block2a_project_… │ (None, 56, 56,  │     2,048 │ block2a_expan… │   N   │
│ (Conv2D)          │ 32)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block2a_project_… │ (None, 56, 56,  │       128 │ block2a_proje… │   N   │
│ (BatchNormalizat… │ 32)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block2b_expand_c… │ (None, 56, 56,  │    36,864 │ block2a_proje… │   N   │
│ (Conv2D)          │ 128)            │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block2b_expand_bn │ (None, 56, 56,  │       512 │ block2b_expan… │   N   │
│ (BatchNormalizat… │ 128)            │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block2b_expand_a… │ (None, 56, 56,  │         0 │ block2b_expan… │   - 

 Total params: 5,944,932 (22.68 MB)

 Trainable params: 25,620 (100.08 KB)

 Non-trainable params: 5,919,312 (22.58 MB)

In [36]:
model.compile(optimizer=Adam(1e-4), loss='categorical_crossentropy', metrics=['accuracy'])
history = model.fit(x_train, y_train, batch_size=32, epochs=5, validation_split = 0.2)

Epoch 1/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 153s 586ms/step - accuracy: 0.0499 - loss: 3.0135 - val_accuracy: 0.0525 - val_loss: 3.0001
Epoch 2/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 129s 518ms/step - accuracy: 0.0528 - loss: 3.0014 - val_accuracy: 0.0525 - val_loss: 2.9998
Epoch 3/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 131s 524ms/step - accuracy: 0.0505 - loss: 3.0009 - val_accuracy: 0.0525 - val_loss: 2.9997
Epoch 4/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 130s 521ms/step - accuracy: 0.0496 - loss: 3.0002 - val_accuracy: 0.0525 - val_loss: 2.9994
Epoch 5/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 129s 517ms/step - accuracy: 0.0529 - loss: 3.0009 - val_accuracy: 0.0525 - val_loss: 2.9995


In [37]:
loss, acc = model.evaluate(x_test, y_test)
print(f"Test Accuracy for EfficientNetV2B0: {acc*100:.2f}%")

63/63 ━━━━━━━━━━━━━━━━━━━━ 26s 406ms/step - accuracy: 0.0528 - loss: 2.9967
Test Accuracy for EfficientNetV2B0: 5.00%


8. InceptionV3

In [25]:
model_inception = InceptionV3(weights='imagenet', include_top=False, input_shape=(224,224,3))
model_inception.trainable = False

In [26]:
inputs = model_inception.input
outputs = model_inception.output
x = GlobalAveragePooling2D()(outputs)
outputs = Dense(20, activation='softmax')(x)
model = Model(inputs, outputs)
model.summary(show_trainable=True)

Model: "functional_8"

┏━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━┳━━━━━━━━━━━━━━━━┳━━━━━━━┓
┃ Layer (type)      ┃ Output Shape    ┃   Param # ┃ Connected to   ┃ Trai… ┃
┡━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━╇━━━━━━━━━━━━━━━━╇━━━━━━━┩
│ input_layer_7     │ (None, 224,     │         0 │ -              │   -   │
│ (InputLayer)      │ 224, 3)         │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ conv2d (Conv2D)   │ (None, 111,     │       864 │ input_layer_7… │   N   │
│                   │ 111, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ batch_normalizat… │ (None, 111,     │        96 │ conv2d[0][0]   │   N   │
│ (BatchNormalizat… │ 111, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ activation_188    │ (None, 111,     │         0 │ batch_normali… │   -   │
│ (Activation)      │ 111, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ conv2d_1 (Conv2D) │ (None, 109,     │     9,216 │ activation_18… │   N   │
│                   │ 109, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ batch_normalizat… │ (None, 109,     │        96 │ conv2d_1[0][0] │   N   │
│ (BatchNormalizat… │ 109, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ activation_189    │ (None, 109,     │         0 │ batch_normali… │   -   │
│ (Activation)      │ 109, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ conv2d_2 (Conv2D) │ (None, 109,     │    18,432 │ activation_18… │   N   │
│                   │ 109, 64)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ batch_normalizat… │ (None, 109,     │       192 │ conv2d_2[0][0] │   N   │
│ (BatchNormalizat… │ 109, 64)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ activation_190    │ (None, 109,     │         0 │ batch_normali… │   -   │
│ (Activation)      │ 109, 64)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ max_pooling2d     │ (None, 54, 54,  │         0 │ activation_19… │   -   │
│ (MaxPooling2D)    │ 64)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ conv2d_3 (Conv2D) │ (None, 54, 54,  │     5,120 │ max_pooling2d… │   N   │
│                   │ 80)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ batch_normalizat… │ (None, 54, 54,  │       240 │ conv2d_3[0][0] │   N   │
│ (BatchNormalizat… │ 80)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ activation_191    │ (None, 54, 54,  │         0 │ batch_normali… │   -   │
│ (Activation)      │ 80)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ conv2d_4 (Conv2D) │ (None, 52, 52,  │   138,240 │ activation_19… │   N   │
│                   │ 192)            │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ batch_normalizat… │ (None, 52, 52,  │       576 │ conv2d_4[0][0] │   N   │
│ (BatchNormalizat… │ 192)            │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ activation_192    │ (None, 52, 52,  │         0 │ batch_normali… │   - 

 Total params: 21,843,764 (83.33 MB)

 Trainable params: 40,980 (160.08 KB)

 Non-trainable params: 21,802,784 (83.17 MB)

In [42]:
model.compile(optimizer=Adam(1e-4), loss='categorical_crossentropy', metrics=['accuracy'])
history = model.fit(x_train, y_train, batch_size=32, epochs=5, validation_split = 0.2)

Epoch 1/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 257s 1s/step - accuracy: 0.6868 - loss: 1.2324 - val_accuracy: 0.7200 - val_loss: 1.0238
Epoch 2/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 247s 988ms/step - accuracy: 0.7456 - loss: 0.9297 - val_accuracy: 0.7480 - val_loss: 0.8917
Epoch 3/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 206s 824ms/step - accuracy: 0.7714 - loss: 0.8017 - val_accuracy: 0.7620 - val_loss: 0.8226
Epoch 4/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 206s 825ms/step - accuracy: 0.7849 - loss: 0.7240 - val_accuracy: 0.7680 - val_loss: 0.7792
Epoch 5/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 207s 827ms/step - accuracy: 0.7970 - loss: 0.6689 - val_accuracy: 0.7730 - val_loss: 0.7490


In [43]:
loss, acc = model.evaluate(x_test, y_test)
print(f"Test Accuracy for InceptionV3: {acc*100:.2f}%")

63/63 ━━━━━━━━━━━━━━━━━━━━ 42s 656ms/step - accuracy: 0.7564 - loss: 0.7832
Test Accuracy for InceptionV3: 74.85%


9. Xception

In [27]:
model_xception = Xception(weights='imagenet', include_top=False, input_shape=(224,224,3))
model_xception.trainable = False

In [28]:
inputs = model_xception.input
outputs = model_xception.output
x = GlobalAveragePooling2D()(outputs)
outputs = Dense(20, activation='softmax')(x)
model = Model(inputs, outputs)
model.summary(show_trainable=True)

Model: "functional_9"

┏━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━┳━━━━━━━━━━━━━━━━┳━━━━━━━┓
┃ Layer (type)      ┃ Output Shape    ┃   Param # ┃ Connected to   ┃ Trai… ┃
┡━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━╇━━━━━━━━━━━━━━━━╇━━━━━━━┩
│ input_layer_8     │ (None, 224,     │         0 │ -              │   -   │
│ (InputLayer)      │ 224, 3)         │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block1_conv1      │ (None, 111,     │       864 │ input_layer_8… │   N   │
│ (Conv2D)          │ 111, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block1_conv1_bn   │ (None, 111,     │       128 │ block1_conv1[… │   N   │
│ (BatchNormalizat… │ 111, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block1_conv1_act  │ (None, 111,     │         0 │ block1_conv1_… │   -   │
│ (Activation)      │ 111, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block1_conv2      │ (None, 109,     │    18,432 │ block1_conv1_… │   N   │
│ (Conv2D)          │ 109, 64)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block1_conv2_bn   │ (None, 109,     │       256 │ block1_conv2[… │   N   │
│ (BatchNormalizat… │ 109, 64)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block1_conv2_act  │ (None, 109,     │         0 │ block1_conv2_… │   -   │
│ (Activation)      │ 109, 64)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block2_sepconv1   │ (None, 109,     │     8,768 │ block1_conv2_… │   N   │
│ (SeparableConv2D) │ 109, 128)       │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block2_sepconv1_… │ (None, 109,     │       512 │ block2_sepcon… │   N   │
│ (BatchNormalizat… │ 109, 128)       │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block2_sepconv2_… │ (None, 109,     │         0 │ block2_sepcon… │   -   │
│ (Activation)      │ 109, 128)       │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block2_sepconv2   │ (None, 109,     │    17,536 │ block2_sepcon… │   N   │
│ (SeparableConv2D) │ 109, 128)       │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block2_sepconv2_… │ (None, 109,     │       512 │ block2_sepcon… │   N   │
│ (BatchNormalizat… │ 109, 128)       │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ conv2d_94         │ (None, 55, 55,  │     8,192 │ block1_conv2_… │   N   │
│ (Conv2D)          │ 128)            │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block2_pool       │ (None, 55, 55,  │         0 │ block2_sepcon… │   -   │
│ (MaxPooling2D)    │ 128)            │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ batch_normalizat… │ (None, 55, 55,  │       512 │ conv2d_94[0][… │   N   │
│ (BatchNormalizat… │ 128)            │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ add_4 (Add)       │ (None, 55, 55,  │         0 │ block2_pool[0… │   -   │
│                   │ 128)            │           │ batch_normali… │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ block3_sepconv1_… │ (None, 55, 55,  │         0 │ add_4[0][0]    │   - 

 Total params: 20,902,460 (79.74 MB)

 Trainable params: 40,980 (160.08 KB)

 Non-trainable params: 20,861,480 (79.58 MB)

In [46]:
model.compile(optimizer=Adam(1e-4), loss='categorical_crossentropy', metrics=['accuracy'])
history = model.fit(x_train, y_train, batch_size=32, epochs=5, validation_split = 0.2)

Epoch 1/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 502s 2s/step - accuracy: 0.2372 - loss: 2.7119 - val_accuracy: 0.6605 - val_loss: 1.7473
Epoch 2/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 438s 2s/step - accuracy: 0.6956 - loss: 1.5786 - val_accuracy: 0.7340 - val_loss: 1.2221
Epoch 3/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 494s 2s/step - accuracy: 0.7439 - loss: 1.1474 - val_accuracy: 0.7550 - val_loss: 1.0054
Epoch 4/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 440s 2s/step - accuracy: 0.7632 - loss: 0.9570 - val_accuracy: 0.7660 - val_loss: 0.8934
Epoch 5/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 440s 2s/step - accuracy: 0.7771 - loss: 0.8510 - val_accuracy: 0.7720 - val_loss: 0.8251


In [47]:
loss, acc = model.evaluate(x_test, y_test)
print(f"Test Accuracy for Xception: {acc*100:.2f}%")

63/63 ━━━━━━━━━━━━━━━━━━━━ 89s 1s/step - accuracy: 0.7744 - loss: 0.8275
Test Accuracy for Xception: 76.70%


10. InceptionResNetV2

In [29]:
model_inceptionv2 = InceptionResNetV2(weights='imagenet', include_top=False, input_shape=(224,224,3))
model_inceptionv2.trainable = False

In [30]:
inputs = model_inceptionv2.input
outputs = model_inceptionv2.output
x = GlobalAveragePooling2D()(outputs)
outputs = Dense(20, activation='softmax')(x)
model = Model(inputs, outputs)
model.summary(show_trainable=True)

Model: "functional_10"

┏━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━┳━━━━━━━━━━━━━━━━┳━━━━━━━┓
┃ Layer (type)      ┃ Output Shape    ┃   Param # ┃ Connected to   ┃ Trai… ┃
┡━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━╇━━━━━━━━━━━━━━━━╇━━━━━━━┩
│ input_layer_9     │ (None, 224,     │         0 │ -              │   -   │
│ (InputLayer)      │ 224, 3)         │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ conv2d_98         │ (None, 111,     │       864 │ input_layer_9… │   N   │
│ (Conv2D)          │ 111, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ batch_normalizat… │ (None, 111,     │        96 │ conv2d_98[0][… │   N   │
│ (BatchNormalizat… │ 111, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ activation_282    │ (None, 111,     │         0 │ batch_normali… │   -   │
│ (Activation)      │ 111, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ conv2d_99         │ (None, 109,     │     9,216 │ activation_28… │   N   │
│ (Conv2D)          │ 109, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ batch_normalizat… │ (None, 109,     │        96 │ conv2d_99[0][… │   N   │
│ (BatchNormalizat… │ 109, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ activation_283    │ (None, 109,     │         0 │ batch_normali… │   -   │
│ (Activation)      │ 109, 32)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ conv2d_100        │ (None, 109,     │    18,432 │ activation_28… │   N   │
│ (Conv2D)          │ 109, 64)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ batch_normalizat… │ (None, 109,     │       192 │ conv2d_100[0]… │   N   │
│ (BatchNormalizat… │ 109, 64)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ activation_284    │ (None, 109,     │         0 │ batch_normali… │   -   │
│ (Activation)      │ 109, 64)        │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ max_pooling2d_4   │ (None, 54, 54,  │         0 │ activation_28… │   -   │
│ (MaxPooling2D)    │ 64)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ conv2d_101        │ (None, 54, 54,  │     5,120 │ max_pooling2d… │   N   │
│ (Conv2D)          │ 80)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ batch_normalizat… │ (None, 54, 54,  │       240 │ conv2d_101[0]… │   N   │
│ (BatchNormalizat… │ 80)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ activation_285    │ (None, 54, 54,  │         0 │ batch_normali… │   -   │
│ (Activation)      │ 80)             │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ conv2d_102        │ (None, 52, 52,  │   138,240 │ activation_28… │   N   │
│ (Conv2D)          │ 192)            │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ batch_normalizat… │ (None, 52, 52,  │       576 │ conv2d_102[0]… │   N   │
│ (BatchNormalizat… │ 192)            │           │                │       │
├───────────────────┼─────────────────┼───────────┼────────────────┼───────┤
│ activation_286    │ (None, 52, 52,  │         0 │ batch_normali… │   - 

 Total params: 54,367,476 (207.40 MB)

 Trainable params: 30,740 (120.08 KB)

 Non-trainable params: 54,336,736 (207.28 MB)

In [50]:
model.compile(optimizer=Adam(1e-4), loss='categorical_crossentropy', metrics=['accuracy'])
history = model.fit(x_train, y_train, batch_size=32, epochs=5, validation_split = 0.2)

Epoch 1/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 483s 2s/step - accuracy: 0.2712 - loss: 2.5983 - val_accuracy: 0.7035 - val_loss: 1.2580
Epoch 2/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 465s 2s/step - accuracy: 0.7224 - loss: 1.1417 - val_accuracy: 0.7565 - val_loss: 0.8808
Epoch 3/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 465s 2s/step - accuracy: 0.7731 - loss: 0.8368 - val_accuracy: 0.7780 - val_loss: 0.7523
Epoch 4/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 465s 2s/step - accuracy: 0.7937 - loss: 0.7158 - val_accuracy: 0.7885 - val_loss: 0.6858
Epoch 5/5
250/250 ━━━━━━━━━━━━━━━━━━━━ 515s 2s/step - accuracy: 0.8091 - loss: 0.6466 - val_accuracy: 0.8005 - val_loss: 0.6439


In [51]:
loss, acc = model.evaluate(x_test, y_test)
print(f"Test Accuracy for InceptionResNetV2: {acc*100:.2f}%")

63/63 ━━━━━━━━━━━━━━━━━━━━ 93s 1s/step - accuracy: 0.7894 - loss: 0.6656
Test Accuracy for InceptionResNetV2: 79.30%


Clear GPU Memory

In [1]:
from tensorflow.keras import backend as K
import gc

K.clear_session()
gc.collect()


2025-05-24 13:58:14.228861: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:467] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1748073494.246274   60202 cuda_dnn.cc:8579] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1748073494.252261   60202 cuda_blas.cc:1407] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
W0000 00:00:1748073494.265016   60202 computation_placer.cc:177] computation placer already registered. Please check linkage and avoid linking the same target more than once.
W0000 00:00:1748073494.265032   60202 computation_placer.cc:177] computation placer already registered. Please check linkage and avoid linking the same target more than once.
W0000 00:00:1748073494.265034   60202 computation_placer.cc:177] computation placer alr

0

In [10]:
source tf-env/bin/activate

SyntaxError: invalid syntax (29176056.py, line 1)